# New York Data

## Step 1: Import Libraries

In [1]:
import numpy as np

import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim

import requests
from pandas.io.json import json_normalize

import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans

import folium

print('Libraries Imported!')

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    geopy-1.21.0               |             py_0          58 KB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.2 MB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.50-py_0
  geopy              conda-forge/noarch::geopy-1.21.0-py_0

The following packages will be UPDATED:

  openssl                                 1.1.1f-h516909a_0 --> 1.1.1g-h516909a_0



openssl-1.1.1g       | 2.1 MB    | ############

In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


## Step 2: Dealing with JSON data to obtan the DataFrame

In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [4]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [5]:
NY_neighborhoods_data = newyork_data['features']

In [6]:
NY_neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [7]:
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude']

NY_neighborhoods = pd.DataFrame(columns = column_names)

In [8]:
NY_neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [9]:
for data in NY_neighborhoods_data:
    borough = data['properties']['borough']
    neighborhood_name = data['properties']['name']
    
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    NY_neighborhoods = NY_neighborhoods.append({'Borough': borough,
                                               'Neighborhood': neighborhood_name,
                                               'Latitude': neighborhood_lat,
                                               'Longitude': neighborhood_lon}, ignore_index = True)

In [15]:
! pip install openpyxl

     |████████████████████████████████| 174kB 6.7MB/s eta 0:00:01
  Stored in directory: /home/jupyterlab/.cache/pip/wheels/b5/85/ca/e768ac132e57e75e645a151f8badac71cc0089e7225dddf76b
  Stored in directory: /home/jupyterlab/.cache/pip/wheels/2a/77/35/0da0965a057698121fc7d8c5a7a9955cdbfb3cc4e2423cad39
Successfully built openpyxl et-xmlfile


In [16]:
import openpyxl
NY_neighborhoods.head()
NY_neighborhoods.to_excel(r'D:\ML\IBM Applied Data Science Capstone Project\NY_data.xlsx', index = None, header=True, encoding = 'utf8-8')

In [17]:
print('The Dataframe has {} boroughs and {} neighborhoods.'.format(
        len(NY_neighborhoods['Borough'].unique()),
        NY_neighborhoods.shape[0]
))

The Dataframe has 5 boroughs and 306 neighborhoods.


In [18]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent = 'ny_explorer')
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

print('The geographical coordinate of New York City are {} {}.'.format(latitude, longitude))

The geographical coordinate of New York City are 40.7127281 -74.0060152.


In [19]:
map_newyork = folium.Map(location = [latitude, longitude], zoom_start = 10)

for lat, lng, borough, neighborhood in zip(NY_neighborhoods['Latitude'], NY_neighborhoods['Longitude'], NY_neighborhoods['Borough'], NY_neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html = True)
    folium.CircleMarker(
        [lat, lng],
        radius = 5,
        popup = label,
        color = 'blue',
        fill = True,
        fill_color = '#3186cc',
        fill_opacity = 0.7,
        parse_html = False).add_to(map_newyork)

map_newyork

In [20]:
CLIENT_ID = '2D1W4Q5ZOVEIQGT1C0X1KEKQTKWJIILO5FTEBCJOQDRNDEIN' # I have removed it after using so as to keep it confidential
CLIENT_SECRET = '2SR3ORF2O1YKHBPYAMZ45QNY0DSDRJLXLX0ZA4IBKZC0TXRY' # I have removed it after using so as to keep it confidential
VERSION = '20180605' # Foursquare API version

print('Your credentails: Sankalp Manoj Gosawi')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails: Sankalp Manoj Gosawi
CLIENT_ID: 2D1W4Q5ZOVEIQGT1C0X1KEKQTKWJIILO5FTEBCJOQDRNDEIN
CLIENT_SECRET:2SR3ORF2O1YKHBPYAMZ45QNY0DSDRJLXLX0ZA4IBKZC0TXRY


In [21]:
LIMIT = 100
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)


In [22]:
NY_venues = getNearbyVenues(names = NY_neighborhoods['Neighborhood'], latitudes = NY_neighborhoods['Latitude'], longitudes = NY_neighborhoods['Longitude'])

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [23]:
print(NY_venues.shape)
NY_venues.head()

(9777, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
2         Walgreens       40.896528       -73.844700        Pharmacy  
3          Rite Aid       40.896649       -73.844846        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [24]:
NY_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      32                      32   
Annadale                                      14                      14   
Arden Heights                                  4                       4   
Arlington                                      7                       7   
Arrochar                                      20                      20   
Arverne                                       17                      17   
Astoria                                       98                      98   
Astoria Heights                               14                      14   
Auburndale                                    18                      18   
Bath Beach                                    49                      49   
Battery Park City                             57                      57   
Bay Ridge                                     88                      88   
Bay Terrace                                   50                      50   
Baychester                                    19                      19   
Bayside                                       70                      70   
Bayswater                                      2                       2   
Bedford Park                                  37                      37   
Bedford Stuyvesant                            27                      27   
Beechhurst                                    12                      12   
Bellaire                                      15                      15   
Belle Harbor                                  17                      17   
Bellerose                                     23                      23   
Belmont                                      100                     100   
Bensonhurst                                   28                      28   
Bergen Beach                                   6                       6   
Blissville                                    17                      17   
Bloomfield                                     5                       5   
Boerum Hill                                   93                      93   
Borough Park                                  19                      19   
Breezy Point                                   4                       4   
Briarwood                                     11                      11   
Brighton Beach                                45                      45   
Broad Channel                                  5                       5   
Broadway Junction                             14                      14   
Bronxdale                                     13                      13   
Brooklyn Heights                             100                     100   
Brookville                                     2                       2   
Brownsville                                   20                      20   
Bulls Head                                    45                      45   
Bushwick                                      72                      72   
Butler Manor                                   6                       6   
Cambria Heights                               11                      11   
Canarsie                                       9                       9   
Carnegie Hill                                 88                      88   
Carroll Gardens                              100                     100   
Castle Hill                                    8                       8   
Castleton Corners                             17                      17   
Central Harlem                                44                      44   
Charleston                                    31                      31   
Chelsea                                      107                     107   
Chinatown                                    100                     100   

In [25]:
print('There are {} unique categories.'.format(len(NY_venues['Venue Category'].unique())))

There are 425 unique categories.


In [26]:
NY_onehot = pd.get_dummies(NY_venues[['Venue Category']], prefix = "", prefix_sep = "")

NY_onehot['Neighborhood'] = NY_venues['Neighborhood']

col_list = list(NY_onehot.columns)
col_list.remove('Neighborhood')
cols = ['Neighborhood'] + [col for col in col_list]

NY_onehot = NY_onehot[cols]

NY_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0    Wakefield                  0               0                  0   
1    Wakefield                  0               0                  0   
2    Wakefield                  0               0                  0   
3    Wakefield                  0               0                  0   
4    Wakefield                  0               0                  0   

   African Restaurant  Airport Terminal  American Restaurant  Animal Shelter  \
0                   0                 0                    0               0   
1                   0                 0                    0               0   
2                   0                 0                    0               0   
3                   0                 0                    0               0   
4                   0                 0                    0               0   

   Antique Shop  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0             0       0                 0                       0   
1             0       0                 0                       0   
2             0       0                 0                       0   
3             0       0                 0                       0   
4             0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  Auto Garage  Automotive Shop  BBQ Joint  Baby Store  \
0                    0            0                0          0           0   
1                    0            0                0          0           0   
2                    0            0                0          0           0   
3                    0            0                0          0           0   
4                    0            0                0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Basketball Stadium  Bath House  Beach  Beach Bar  \
0                 0                   0           0      0          0   
1                 0                   0           0      0          0   
2                 0                   0           0      0          0   
3                 0                   0           0      0          0   
4                 0                   0           0      0          0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0         0            0           0              0                         0   
1         0            0           0              0                         0   
2         0            0           0              0                         0   
3         0            0           0              0                         0   
4         0            0 

In [27]:
NY_onehot.shape

(9777, 425)

In [28]:
NY_grouped = NY_onehot.groupby('Neighborhood').mean().reset_index()
NY_grouped

Neighborhood  Accessories Store  Adult Boutique  \
0                     Allerton           0.000000        0.000000   
1                     Annadale           0.000000        0.000000   
2                Arden Heights           0.000000        0.000000   
3                    Arlington           0.000000        0.000000   
4                     Arrochar           0.000000        0.000000   
5                      Arverne           0.000000        0.000000   
6                      Astoria           0.000000        0.000000   
7              Astoria Heights           0.000000        0.000000   
8                   Auburndale           0.000000        0.000000   
9                   Bath Beach           0.000000        0.000000   
10           Battery Park City           0.000000        0.000000   
11                   Bay Ridge           0.000000        0.000000   
12                 Bay Terrace           0.020000        0.000000   
13                  Baychester           0.000000        0.000000   
14                     Bayside           0.000000        0.000000   
15                   Bayswater           0.000000        0.000000   
16                Bedford Park           0.000000        0.000000   
17          Bedford Stuyvesant           0.000000        0.000000   
18                  Beechhurst           0.000000        0.000000   
19                    Bellaire           0.000000        0.000000   
20                Belle Harbor           0.000000        0.000000   
21                   Bellerose           0.000000        0.000000   
22                     Belmont           0.000000        0.000000   
23                 Bensonhurst           0.000000        0.000000   
24                Bergen Beach           0.000000        0.000000   
25                  Blissville           0.000000        0.000000   
26                  Bloomfield           0.000000        0.000000   
27                 Boerum Hill           0.000000        0.000000   
28                Borough Park           0.000000        0.000000   
29                Breezy Point           0.000000        0.000000   
30                   Briarwood           0.000000        0.000000   
31              Brighton Beach           0.000000        0.000000   
32               Broad Channel           0.000000        0.000000   
33           Broadway Junction           0.000000        0.000000   
34                   Bronxdale           0.000000        0.000000   
35            Brooklyn Heights           0.000000        0.000000   
36                  Brookville           0.000000        0.000000   
37                 Brownsville           0.000000        0.000000   
38                  Bulls Head           0.000000        0.000000   
39                    Bushwick           0.000000        0.000000   
40                Butler Manor           0.000000        0.000000   
41             Cambria Heights           0.000000        0.000000   
42                    Canarsie           0.000000        0.000000   
43               Carnegie Hill           0.000000        0.000000   
44             Carroll Gardens           0.000000        0.000000   
45                 Castle Hill           0.000000        0.000000   
46           Castleton Corners           0.000000        0.000000   
47              Central Harlem           0.000000        0.000000   
48                  Charleston           0.000000        0.000000   
49                     Chelsea           0.000000        0.000000   
50                   Chinatown           0.000000        0.000000   
51                 City Island           0.000000        0.000000   
52                   City Line           0.000000        0.000000   
53                Civic Center           0.000000        0.000000   
54           Claremont Village           0.000000        0.000000   
55                Clason Point           0.000000        0.000000   
56                     Clifton           0.000000        0.000000   
57              

In [29]:
NY_grouped.shape

(300, 425)

In [30]:
export_excel = NY_grouped.to_excel(r'D:\ML\IBM Applied Data Science Capstone Project\NY_grouped.xlsx', index = None, header=True, encoding = 'utf8-8')